In [25]:
## Importing required libraries
import sqlite3
import pandas as pd
import numpy as np
import itertools
import matplotlib.pyplot as plt
from sklearn.linear_model import RidgeClassifier
from sklearn.linear_model import SGDClassifier
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.ensemble import AdaBoostClassifier 
from sklearn.ensemble import RandomForestClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.neighbors import KNeighborsClassifier
from sklearn.linear_model import LinearRegression
from sklearn.metrics import confusion_matrix
from sklearn.metrics import classification_report, accuracy_score
from sklearn.calibration import CalibratedClassifierCV
from sklearn import model_selection
from sklearn.model_selection import train_test_split
from sklearn.metrics import make_scorer
from sklearn.preprocessing import StandardScaler
from time import time
from sklearn.decomposition import PCA, FastICA
from sklearn.pipeline import Pipeline
pd.options.mode.chained_assignment = None

In [26]:
## Fetching data
#Connecting to database
database = './.gitignore/database.sqlite'
conn = sqlite3.connect(database)

#Fetching required data tables
#player_data = pd.read_sql("SELECT * FROM Player;", conn)
player_attributes = pd.read_sql("SELECT * FROM Player_Attributes;", conn)
#team_data = pd.read_sql("SELECT * FROM Team;", conn)
match_data = pd.read_sql("SELECT * FROM Match;", conn)

#Reduce match data to fulfill run time requirements
rows = ["country_id", "league_id", "season", "stage", "date", "match_api_id", "home_team_api_id", 
        "away_team_api_id", "home_team_goal", "away_team_goal", "home_player_1", "home_player_2",
        "home_player_3", "home_player_4", "home_player_5", "home_player_6", "home_player_7", 
        "home_player_8", "home_player_9", "home_player_10", "home_player_11", "away_player_1",
        "away_player_2", "away_player_3", "away_player_4", "away_player_5", "away_player_6",
        "away_player_7", "away_player_8", "away_player_9", "away_player_10", "away_player_11"]

#Dictionary to convert player IDs to names
'''playerDict = {}
i = 0
for playerID in player_data['player_api_id']:
    playerDict[playerID] =  player_data['player_name'][i]
    i += 1'''

"playerDict = {}\ni = 0\nfor playerID in player_data['player_api_id']:\n    playerDict[playerID] =  player_data['player_name'][i]\n    i += 1"

In [27]:
nameRows = ["home_player_1", "home_player_2",
        "home_player_3", "home_player_4", "home_player_5", "home_player_6", "home_player_7", 
        "home_player_8", "home_player_9", "home_player_10", "home_player_11", "away_player_1",
        "away_player_2", "away_player_3", "away_player_4", "away_player_5", "away_player_6",
        "away_player_7", "away_player_8", "away_player_9", "away_player_10", "away_player_11"]

In [28]:
playerRatingDict = {}
i = 0
for playerID in player_attributes['player_api_id']:
    if playerID in playerRatingDict:
        i += 1
    else:
        playerRatingDict[playerID] =  player_attributes['overall_rating'][i]
        i += 1
'''
for playerRow in nameRows:
    colName = str(playerRow) + '_name'
    nameRows.append(colName)'''

"\nfor playerRow in nameRows:\n    colName = str(playerRow) + '_name'\n    nameRows.append(colName)"

In [29]:
# To make a new Datafram with no nan values for player IDs
new_match_data = match_data.dropna(subset=nameRows, inplace=False, how='any')


In [30]:
new_match_data['home_mean_rating'] = pd.Series()
new_match_data['away_mean_rating'] = pd.Series()
for index in new_match_data.index:
    new_match_data['home_mean_rating'][index] =  (playerRatingDict[new_match_data['home_player_1'][index]]+
                                                playerRatingDict[new_match_data['home_player_2'][index]]+
                                                playerRatingDict[new_match_data['home_player_3'][index]]+
                                                playerRatingDict[new_match_data['home_player_4'][index]]+
                                                playerRatingDict[new_match_data['home_player_5'][index]]+
                                                playerRatingDict[new_match_data['home_player_6'][index]]+
                                                playerRatingDict[new_match_data['home_player_7'][index]]+
                                                playerRatingDict[new_match_data['home_player_8'][index]]+
                                                playerRatingDict[new_match_data['home_player_9'][index]]+
                                                playerRatingDict[new_match_data['home_player_10'][index]]+
                                                playerRatingDict[new_match_data['home_player_11'][index]] ) / 11
                                                                  
    new_match_data['away_mean_rating'][index] = (playerRatingDict[new_match_data['away_player_1'][index]]+
                                                playerRatingDict[new_match_data['away_player_2'][index]]+
                                                playerRatingDict[new_match_data['away_player_3'][index]]+
                                                playerRatingDict[new_match_data['away_player_4'][index]]+
                                                playerRatingDict[new_match_data['away_player_5'][index]]+
                                                playerRatingDict[new_match_data['away_player_6'][index]]+
                                                playerRatingDict[new_match_data['away_player_7'][index]]+
                                                playerRatingDict[new_match_data['away_player_8'][index]]+
                                                playerRatingDict[new_match_data['away_player_9'][index]]+
                                                playerRatingDict[new_match_data['away_player_10'][index]]+
                                                playerRatingDict[new_match_data['away_player_11'][index]] ) / 11
    

In [31]:
def resultFinder(homeScore, awayScore):
    if (homeScore > awayScore):
        return int(1)
    elif (homeScore == awayScore):
        return int(0)
    else: 
        return int(-1)

new_match_data['result'] = pd.Series()    
    
for i in new_match_data.index:
    new_match_data['result'][i] = resultFinder(match_data['home_team_goal'][i], match_data['away_team_goal'][i])

In [32]:
data_of_interest = pd.DataFrame()
data_of_interest['home_rating'] = new_match_data['home_mean_rating']
data_of_interest['away_rating'] = new_match_data['away_mean_rating']
data_of_interest['result'] = new_match_data['result']

array = data_of_interest.values
array_std = StandardScaler().fit_transform(array)


X = array_std[:, 0:-1]
Y = array_std[:, -1]
Y = Y.astype(int)


n = 10
seed = 5

# prepare models
models = [('SGDC', SGDClassifier()),('GBC', GradientBoostingClassifier()),
          ('AdaBC', AdaBoostClassifier()),('RFC', RandomForestClassifier()),
          ('NB', GaussianNB()),('KNC', KNeighborsClassifier()), ('RC', RidgeClassifier()),
          ('CCCV', CalibratedClassifierCV()), ('LR', LinearRegression())]

#evaluate each model
results = []
names = []

for name, model in models:
    kfold = model_selection.KFold(n_splits=n, shuffle=False, random_state=seed)
    cv_results = model_selection.cross_val_score(model, X, Y, cv=kfold)
    
    results.append(cv_results)
    names.append(name)
    
    print('%s: %.2f%% (%f)' %(name, cv_results.mean()*100, cv_results.std()))

SGDC: 71.43% (0.037654)
GBC: 73.76% (0.009006)
AdaBC: 73.61% (0.008139)
RFC: 67.02% (0.006510)
NB: 72.12% (0.015125)
KNC: 70.47% (0.009745)
RC: 73.77% (0.008424)
CCCV: 73.87% (0.008852)
LR: 12.74% (0.025886)


In [126]:
cols_to_remove = ["home_player_1", "home_player_2", "home_player_3", "home_player_4", 
                        "home_player_5", "home_player_6", "home_player_7", "home_player_8", 
                        "home_player_9", "home_player_10", "home_player_11", "away_player_1", 
                        "away_player_2", "away_player_3", "away_player_4", "away_player_5", 
                        "away_player_6", "away_player_7", "away_player_8", "away_player_9", 
                        "away_player_10", "away_player_11", "home_player_X1", "home_player_X2", 
                        "home_player_X3", "home_player_X4", "home_player_X5", "home_player_X6", 
                        "home_player_X7", "home_player_X8", "home_player_X9", "home_player_X10", 
                        "home_player_X11", "away_player_X1", "away_player_X2", "away_player_X3", 
                        "away_player_X4", "away_player_X5", "away_player_X6", "away_player_X7", 
                        "away_player_X8", "away_player_X9", "away_player_X10", "away_player_X11",
                        "home_player_Y1", "home_player_Y2", "home_player_Y3", "home_player_Y4", 
                        "home_player_Y5", "home_player_Y6", "home_player_Y7", "home_player_Y8", 
                        "home_player_Y9", "home_player_Y10", "home_player_Y11", "away_player_Y1", 
                        "away_player_Y2", "away_player_Y3", "away_player_Y4", "away_player_Y5", 
                        "away_player_Y6", "away_player_Y7", "away_player_Y8", "away_player_Y9", 
                        "away_player_Y10", "away_player_Y11"]

match_data.drop(cols_to_remove, axis=1, inplace=True)

In [127]:
rows = ["home_team_goal", "away_team_goal", 'B365H', 'B365D',
       'B365A', 'BWH', 'BWD', 'BWA', 'IWH', 'IWD', 'IWA', 'LBH', 'LBD', 'LBA',
       'PSH', 'PSD', 'PSA', 'WHH', 'WHD', 'WHA', 'SJH', 'SJD', 'SJA', 'VCH',
       'VCD', 'VCA', 'GBH', 'GBD', 'GBA', 'BSH', 'BSD', 'BSA']

print(match_data.shape)

(25979, 49)


In [128]:
match_data.dropna(subset=rows, inplace=True, how='any')
print(match_data.shape)
def resultFinder(homeScore, awayScore):
    if (homeScore > awayScore):
        return int(1)
    elif (homeScore == awayScore):
        return int(0)
    else: 
        return int(-1)

match_data['result'] = pd.Series()    
    
for i in match_data.index:
    match_data['result'][i] = resultFinder(match_data['home_team_goal'][i], match_data['away_team_goal'][i])

(2756, 49)


In [130]:
array = match_data.values[:,19:]

X = array[:, 0:-1]
Y = array[:, -1]
Y = Y.astype(int)


n = 10
seed = 5

# prepare models
models = [('SGDC', SGDClassifier()),('GBC', GradientBoostingClassifier()),
          ('AdaBC', AdaBoostClassifier()),('RFC', RandomForestClassifier()),
          ('NB', GaussianNB()),('KNC', KNeighborsClassifier()), ('RC', RidgeClassifier()),
          ('CCCV', CalibratedClassifierCV())]

#evaluate each model
results = []
names = []

for name, model in models:
    kfold = model_selection.KFold(n_splits=n, shuffle=False, random_state=seed)
    cv_results = model_selection.cross_val_score(model, X, Y, cv=kfold)
    
    results.append(cv_results)
    names.append(name)
    
    print('%s: %.2f%% (%f)' %(name, cv_results.mean()*100, cv_results.std()))

SGDC: 36.94% (0.083049)
GBC: 50.80% (0.034927)
AdaBC: 49.86% (0.035416)
RFC: 44.30% (0.038264)
NB: 41.84% (0.044817)
KNC: 41.83% (0.025383)
RC: 50.72% (0.034204)
CCCV: 50.51% (0.034655)


In [132]:
array = match_data.values[:,19:]
array_std = StandardScaler().fit_transform(array)

X = array_std[:, 0:-1]
Y = array_std[:, -1]
Y = Y.astype(int)


n = 10
seed = 5

# prepare models
models = [('SGDC', SGDClassifier()),('GBC', GradientBoostingClassifier()),
          ('AdaBC', AdaBoostClassifier()),('RFC', RandomForestClassifier()),
          ('NB', GaussianNB()),('KNC', KNeighborsClassifier()), ('RC', RidgeClassifier()),
          ('CCCV', CalibratedClassifierCV()), ('LR', LinearRegression())]

#evaluate each model
results = []
names = []

for name, model in models:
    kfold = model_selection.KFold(n_splits=n, shuffle=False, random_state=seed)
    cv_results = model_selection.cross_val_score(model, X, Y, cv=kfold)
    
    results.append(cv_results)
    names.append(name)
    
    print('%s: %.2f%% (%f)' %(name, cv_results.mean()*100, cv_results.std()))

/Users/AshutoshSinha/anaconda/lib/python3.6/site-packages/sklearn/utils/validation.py:429: DataConversionWarning: Data with input dtype object was converted to float64 by StandardScaler.
  warnings.warn(msg, _DataConversionWarning)


SGDC: 43.76% (0.077558)
GBC: 50.58% (0.036799)
AdaBC: 49.86% (0.035416)
RFC: 44.70% (0.028331)
NB: 41.84% (0.044817)
KNC: 43.29% (0.033588)
RC: 50.69% (0.033835)
CCCV: 50.83% (0.037945)
LR: 12.48% (0.051622)


In [140]:
print(player_attributes.columns)

Index(['id', 'player_fifa_api_id', 'player_api_id', 'date', 'overall_rating',
       'potential', 'preferred_foot', 'attacking_work_rate',
       'defensive_work_rate', 'crossing', 'finishing', 'heading_accuracy',
       'short_passing', 'volleys', 'dribbling', 'curve', 'free_kick_accuracy',
       'long_passing', 'ball_control', 'acceleration', 'sprint_speed',
       'agility', 'reactions', 'balance', 'shot_power', 'jumping', 'stamina',
       'strength', 'long_shots', 'aggression', 'interceptions', 'positioning',
       'vision', 'penalties', 'marking', 'standing_tackle', 'sliding_tackle',
       'gk_diving', 'gk_handling', 'gk_kicking', 'gk_positioning',
       'gk_reflexes'],
      dtype='object')


In [141]:
for idNum in player_attributes['player_api_id']:
    if idNum in playerDict:
        print("ID: %d || Name: %s" %(idNum, playerDict[idNum]))
    else:
        pass

ID: 505942 || Name: Aaron Appindangoye
ID: 505942 || Name: Aaron Appindangoye
ID: 505942 || Name: Aaron Appindangoye
ID: 505942 || Name: Aaron Appindangoye
ID: 505942 || Name: Aaron Appindangoye
ID: 155782 || Name: Aaron Cresswell
ID: 155782 || Name: Aaron Cresswell
ID: 155782 || Name: Aaron Cresswell
ID: 155782 || Name: Aaron Cresswell
ID: 155782 || Name: Aaron Cresswell
ID: 155782 || Name: Aaron Cresswell
ID: 155782 || Name: Aaron Cresswell
ID: 155782 || Name: Aaron Cresswell
ID: 155782 || Name: Aaron Cresswell
ID: 155782 || Name: Aaron Cresswell
ID: 155782 || Name: Aaron Cresswell
ID: 155782 || Name: Aaron Cresswell
ID: 155782 || Name: Aaron Cresswell
ID: 155782 || Name: Aaron Cresswell
ID: 155782 || Name: Aaron Cresswell
ID: 155782 || Name: Aaron Cresswell
ID: 155782 || Name: Aaron Cresswell
ID: 155782 || Name: Aaron Cresswell
ID: 155782 || Name: Aaron Cresswell
ID: 155782 || Name: Aaron Cresswell
ID: 155782 || Name: Aaron Cresswell
ID: 155782 || Name: Aaron Cresswell
ID: 155782 ||

ID: 29904 || Name: Abel Gomez
ID: 29904 || Name: Abel Gomez
ID: 29904 || Name: Abel Gomez
ID: 29904 || Name: Abel Gomez
ID: 29904 || Name: Abel Gomez
ID: 29904 || Name: Abel Gomez
ID: 29904 || Name: Abel Gomez
ID: 29904 || Name: Abel Gomez
ID: 29904 || Name: Abel Gomez
ID: 29904 || Name: Abel Gomez
ID: 29904 || Name: Abel Gomez
ID: 29904 || Name: Abel Gomez
ID: 29904 || Name: Abel Gomez
ID: 29904 || Name: Abel Gomez
ID: 29904 || Name: Abel Gomez
ID: 29904 || Name: Abel Gomez
ID: 29904 || Name: Abel Gomez
ID: 29904 || Name: Abel Gomez
ID: 29904 || Name: Abel Gomez
ID: 105548 || Name: Abel Hernandez
ID: 105548 || Name: Abel Hernandez
ID: 105548 || Name: Abel Hernandez
ID: 105548 || Name: Abel Hernandez
ID: 105548 || Name: Abel Hernandez
ID: 105548 || Name: Abel Hernandez
ID: 105548 || Name: Abel Hernandez
ID: 105548 || Name: Abel Hernandez
ID: 105548 || Name: Abel Hernandez
ID: 105548 || Name: Abel Hernandez
ID: 105548 || Name: Abel Hernandez
ID: 105548 || Name: Abel Hernandez
ID: 105548

ID: 160447 || Name: Adam Smith
ID: 160447 || Name: Adam Smith
ID: 160447 || Name: Adam Smith
ID: 160447 || Name: Adam Smith
ID: 160447 || Name: Adam Smith
ID: 160447 || Name: Adam Smith
ID: 160447 || Name: Adam Smith
ID: 160447 || Name: Adam Smith
ID: 160447 || Name: Adam Smith
ID: 160447 || Name: Adam Smith
ID: 160447 || Name: Adam Smith
ID: 160447 || Name: Adam Smith
ID: 160447 || Name: Adam Smith
ID: 160447 || Name: Adam Smith
ID: 160447 || Name: Adam Smith
ID: 160447 || Name: Adam Smith
ID: 160447 || Name: Adam Smith
ID: 36774 || Name: Adam Szalai
ID: 36774 || Name: Adam Szalai
ID: 36774 || Name: Adam Szalai
ID: 36774 || Name: Adam Szalai
ID: 36774 || Name: Adam Szalai
ID: 36774 || Name: Adam Szalai
ID: 36774 || Name: Adam Szalai
ID: 36774 || Name: Adam Szalai
ID: 36774 || Name: Adam Szalai
ID: 36774 || Name: Adam Szalai
ID: 36774 || Name: Adam Szalai
ID: 36774 || Name: Adam Szalai
ID: 36774 || Name: Adam Szalai
ID: 36774 || Name: Adam Szalai
ID: 36774 || Name: Adam Szalai
ID: 3677

ID: 232103 || Name: Ahmed Musa
ID: 232103 || Name: Ahmed Musa
ID: 232103 || Name: Ahmed Musa
ID: 232103 || Name: Ahmed Musa
ID: 232103 || Name: Ahmed Musa
ID: 232103 || Name: Ahmed Musa
ID: 232103 || Name: Ahmed Musa
ID: 232103 || Name: Ahmed Musa
ID: 232103 || Name: Ahmed Musa
ID: 232103 || Name: Ahmed Musa
ID: 232103 || Name: Ahmed Musa
ID: 232103 || Name: Ahmed Musa
ID: 232103 || Name: Ahmed Musa
ID: 174597 || Name: Ahmed Saied Okka
ID: 174597 || Name: Ahmed Saied Okka
ID: 174597 || Name: Ahmed Saied Okka
ID: 174597 || Name: Ahmed Saied Okka
ID: 174600 || Name: Ahmed Samir Farag
ID: 174600 || Name: Ahmed Samir Farag
ID: 174600 || Name: Ahmed Samir Farag
ID: 174600 || Name: Ahmed Samir Farag
ID: 174600 || Name: Ahmed Samir Farag
ID: 174600 || Name: Ahmed Samir Farag
ID: 174600 || Name: Ahmed Samir Farag
ID: 148953 || Name: Ahmed Soukouna
ID: 148953 || Name: Ahmed Soukouna
ID: 148953 || Name: Ahmed Soukouna
ID: 148953 || Name: Ahmed Soukouna
ID: 441166 || Name: Ahmet Ozcan
ID: 441166 

ID: 88521 || Name: Alberto Rodriguez
ID: 88521 || Name: Alberto Rodriguez
ID: 88521 || Name: Alberto Rodriguez
ID: 88521 || Name: Alberto Rodriguez
ID: 88521 || Name: Alberto Rodriguez
ID: 88521 || Name: Alberto Rodriguez
ID: 88521 || Name: Alberto Rodriguez
ID: 88521 || Name: Alberto Rodriguez
ID: 88521 || Name: Alberto Rodriguez
ID: 38576 || Name: Alberto Zapater
ID: 38576 || Name: Alberto Zapater
ID: 38576 || Name: Alberto Zapater
ID: 38576 || Name: Alberto Zapater
ID: 38576 || Name: Alberto Zapater
ID: 38576 || Name: Alberto Zapater
ID: 38576 || Name: Alberto Zapater
ID: 38576 || Name: Alberto Zapater
ID: 38576 || Name: Alberto Zapater
ID: 38576 || Name: Alberto Zapater
ID: 38576 || Name: Alberto Zapater
ID: 38576 || Name: Alberto Zapater
ID: 38576 || Name: Alberto Zapater
ID: 38576 || Name: Alberto Zapater
ID: 38576 || Name: Alberto Zapater
ID: 38576 || Name: Alberto Zapater
ID: 38576 || Name: Alberto Zapater
ID: 38576 || Name: Alberto Zapater
ID: 38576 || Name: Alberto Zapater
ID

...

ID: 102626 || Name: Vasco Fernandes
ID: 102626 || Name: Vasco Fernandes
ID: 163918 || Name: Vasco Regini
ID: 163918 || Name: Vasco Regini
ID: 163918 || Name: Vasco Regini
ID: 163918 || Name: Vasco Regini
ID: 163918 || Name: Vasco Regini
ID: 163918 || Name: Vasco Regini
ID: 163918 || Name: Vasco Regini
ID: 163918 || Name: Vasco Regini
ID: 163918 || Name: Vasco Regini
ID: 163918 || Name: Vasco Regini
ID: 163918 || Name: Vasco Regini
ID: 163918 || Name: Vasco Regini
ID: 163918 || Name: Vasco Regini
ID: 163918 || Name: Vasco Regini
ID: 163918 || Name: Vasco Regini
ID: 163918 || Name: Vasco Regini
ID: 163918 || Name: Vasco Regini
ID: 163918 || Name: Vasco Regini
ID: 163918 || Name: Vasco Regini
ID: 163918 || Name: Vasco Regini
ID: 163918 || Name: Vasco Regini
ID: 163918 || Name: Vasco Regini
ID: 163918 || Name: Vasco Regini
ID: 163918 || Name: Vasco Regini
ID: 470362 || Name: Vasco Rocha
ID: 470362 || Name: Vasco Rocha
ID: 470362 || Name: Vasco Rocha
ID: 210029 || Name: Vasil Shkurtaj
ID: 2

ID: 34662 || Name: Vitor Lima
ID: 34662 || Name: Vitor Lima
ID: 34662 || Name: Vitor Lima
ID: 96846 || Name: Vitor Moreno
ID: 96846 || Name: Vitor Moreno
ID: 96846 || Name: Vitor Moreno
ID: 96846 || Name: Vitor Moreno
ID: 45357 || Name: Vitor Vinha
ID: 45357 || Name: Vitor Vinha
ID: 45357 || Name: Vitor Vinha
ID: 45357 || Name: Vitor Vinha
ID: 45357 || Name: Vitor Vinha
ID: 45357 || Name: Vitor Vinha
ID: 45357 || Name: Vitor Vinha
ID: 45357 || Name: Vitor Vinha
ID: 45357 || Name: Vitor Vinha
ID: 186669 || Name: Vitor
ID: 186669 || Name: Vitor
ID: 186669 || Name: Vitor
ID: 186669 || Name: Vitor
ID: 186669 || Name: Vitor
ID: 186669 || Name: Vitor
ID: 186669 || Name: Vitor
ID: 186669 || Name: Vitor
ID: 186669 || Name: Vitor
ID: 186669 || Name: Vitor
ID: 186669 || Name: Vitor
ID: 186669 || Name: Vitor
ID: 186669 || Name: Vitor
ID: 186669 || Name: Vitor
ID: 186669 || Name: Vitor
ID: 186669 || Name: Vitor
ID: 186669 || Name: Vitor
ID: 186669 || Name: Vitor
ID: 94281 || Name: Vittorio Villano

ID: 210451 || Name: Wesley Lautoa
ID: 210451 || Name: Wesley Lautoa
ID: 656562 || Name: Wesley Moraes Ferreira Da Silva
ID: 656562 || Name: Wesley Moraes Ferreira Da Silva
ID: 656562 || Name: Wesley Moraes Ferreira Da Silva
ID: 656562 || Name: Wesley Moraes Ferreira Da Silva
ID: 445856 || Name: Wesley Said
ID: 445856 || Name: Wesley Said
ID: 445856 || Name: Wesley Said
ID: 445856 || Name: Wesley Said
ID: 445856 || Name: Wesley Said
ID: 445856 || Name: Wesley Said
ID: 445856 || Name: Wesley Said
ID: 445856 || Name: Wesley Said
ID: 445856 || Name: Wesley Said
ID: 445856 || Name: Wesley Said
ID: 445856 || Name: Wesley Said
ID: 445856 || Name: Wesley Said
ID: 445856 || Name: Wesley Said
ID: 445856 || Name: Wesley Said
ID: 30878 || Name: Wesley Sneijder
ID: 30878 || Name: Wesley Sneijder
ID: 30878 || Name: Wesley Sneijder
ID: 30878 || Name: Wesley Sneijder
ID: 30878 || Name: Wesley Sneijder
ID: 30878 || Name: Wesley Sneijder
ID: 30878 || Name: Wesley Sneijder
ID: 30878 || Name: Wesley Sneij

ID: 179795 || Name: Yacine Brahimi
ID: 179795 || Name: Yacine Brahimi
ID: 179795 || Name: Yacine Brahimi
ID: 179795 || Name: Yacine Brahimi
ID: 179795 || Name: Yacine Brahimi
ID: 179795 || Name: Yacine Brahimi
ID: 179795 || Name: Yacine Brahimi
ID: 179795 || Name: Yacine Brahimi
ID: 179795 || Name: Yacine Brahimi
ID: 179795 || Name: Yacine Brahimi
ID: 179795 || Name: Yacine Brahimi
ID: 179795 || Name: Yacine Brahimi
ID: 179795 || Name: Yacine Brahimi
ID: 179795 || Name: Yacine Brahimi
ID: 179795 || Name: Yacine Brahimi
ID: 179795 || Name: Yacine Brahimi
ID: 179795 || Name: Yacine Brahimi
ID: 179795 || Name: Yacine Brahimi
ID: 179795 || Name: Yacine Brahimi
ID: 179795 || Name: Yacine Brahimi
ID: 179795 || Name: Yacine Brahimi
ID: 179795 || Name: Yacine Brahimi
ID: 179795 || Name: Yacine Brahimi
ID: 179795 || Name: Yacine Brahimi
ID: 179795 || Name: Yacine Brahimi
ID: 179795 || Name: Yacine Brahimi
ID: 179795 || Name: Yacine Brahimi
ID: 179795 || Name: Yacine Brahimi
ID: 179795 || Name: 

ID: 25538 || Name: Youssouf Hadji
ID: 25538 || Name: Youssouf Hadji
ID: 25538 || Name: Youssouf Hadji
ID: 25538 || Name: Youssouf Hadji
ID: 26609 || Name: Youssouf Hersi
ID: 26609 || Name: Youssouf Hersi
ID: 26609 || Name: Youssouf Hersi
ID: 26609 || Name: Youssouf Hersi
ID: 26609 || Name: Youssouf Hersi
ID: 26609 || Name: Youssouf Hersi
ID: 26609 || Name: Youssouf Hersi
ID: 26609 || Name: Youssouf Hersi
ID: 26609 || Name: Youssouf Hersi
ID: 26609 || Name: Youssouf Hersi
ID: 26609 || Name: Youssouf Hersi
ID: 26609 || Name: Youssouf Hersi
ID: 26609 || Name: Youssouf Hersi
ID: 26609 || Name: Youssouf Hersi
ID: 26609 || Name: Youssouf Hersi
ID: 26609 || Name: Youssouf Hersi
ID: 26609 || Name: Youssouf Hersi
ID: 26609 || Name: Youssouf Hersi
ID: 26609 || Name: Youssouf Hersi
ID: 467689 || Name: Youssouf Sabaly
ID: 467689 || Name: Youssouf Sabaly
ID: 467689 || Name: Youssouf Sabaly
ID: 467689 || Name: Youssouf Sabaly
ID: 467689 || Name: Youssouf Sabaly
ID: 467689 || Name: Youssouf Sabaly
ID